In [6]:
import pandas as pd

In [ ]:
enru = pd.read_csv("./lookup results/yandex_lookup_en_ru_lemmas_only_WHOLE_LIST.csv")

In [ ]:
enru.info()

In [ ]:
enru.head(10)

In [ ]:
enrufr_naive = pd.read_csv("./lookup results/naive_transaltion_en_ru_fr_LEMMAS_WHOLE_LIST.csv")
enrufr_naive.head()

In [ ]:
enrufr_naive['russian_word'] = list(enru['local_word'])

In [ ]:
del (enrufr_naive['Unnamed: 0'])
enrufr_naive.head()

In [ ]:
column = ['word','russian_word', 'local_word','examples','local_examples']
enrufr_naive = enrufr_naive.reindex(columns=column)

In [ ]:
enrufr_naive.head(60)

In [ ]:
enrufr_naive.to_csv("enrufr_naive_transation_yandex_lookup_whole_list.csv")

# match systran en ru vs en fr

In [7]:
systran_en_fr = pd.read_csv("systran_en_fr.csv")
systran_en_fr.head()

Unnamed: 0  word local_word  \
0           0  word        mot   
1           1  word     parole   
2           2  word      terme   
3           3  word     propos   
4           4  word    mention   

                                            examples  \
0        key word|last word|signal word|first words|   
1  fine words|word of god|kind word|word of the l...   
2  following words|search word|operative word|eng...   
3    written word|wise words|clear words|warm words|   
4                               words of limitation|   

                                      local_examples  \
0  mot clé | dernier mot | mot indicateur | premi...   
1  belle parole | parole de dieu | aimables parol...   
2  termes suivants | terme de recherche | terme p...   
3  propos écrits ici | propos sages | propos clai...   
4                           mention de limitation |    

                            examples_and_definitions  
0  key word|last word|signal word|first words|ter...  
1  fine words|word of god|kind word|word of the l...  
2  following words|search word|operative word|eng...  
3  written word|wise words|clear words|warm words...  
4  words of limitation|particular | reference | m...

In [8]:
systran_en_ru = pd.read_csv("systran_en_ru.csv")
systran_en_ru.head(20)

Unnamed: 0  word                   local_word  \
0            0  word                        слово   
1            1   and                            и   
2            2   and                            а   
3            3   and                            и   
4            4   and                           но   
5            5   and                            а   
6            6  that                          так   
7            7  that                           то   
8            8  that  который / кто / тот который   
9            9  that                          тот   
10          10  that                          что   
11          11  that                        чтобы   
12          12   for                          для   
13          13   for                           на   
14          14   for                           за   
15          15   for                            в   
16          16   for                           по   
17          17   for                            к   
18          18   for             потому что / ибо   
19          19  with                            с   

                                             examples  \
0         key word|english word|first word|good word|   
1                                          empty_cell   
2                                          empty_cell   
3                     He thinks of you day and night|   
4        It's an embarrassing joke and not an insult|   
5                 This is a squid and not an octopus|   
6                                          empty_cell   
7                                          empty_cell   
8              I know the guy that sold you the disk|   
9   On that evening I met Natalie|Do you see those...   
10          Tell him that Margaret wanted to see him|   
11  Turn the mirror so that the room becomes visua...   
12                                         empty_cell   
13                                         empty_cell   
14                                         empty_cell   
15                                         empty_cell   
16                                         empty_cell   
17                                         empty_cell   
18                  Lord forgive me, for I've sinned|   
19                                         empty_cell   

                                       local_examples  \
0   ключевое слово | английское слово | первое сло...   
1                                          empty_cell   
2                                          empty_cell   
3                      Он думает о вас день и ночь |    
4           Это неуместная шутка, а не оскорбление |    
5                       Это кальмар, а не осьминог |    
6                                          empty_cell   
7                                          empty_cell   
8           Я знаю парня, который продал тебе диск |    
9   В тот вечер я встретил Натали | Видишь те две ...   
10    Скажите ему, что Марагарет хотела видеть его |    
11  Поверните зеркало, так чтобы комната казалась ...   
12                                         empty_cell   
13                                         empty_cell   
14                                         empty_cell   
15                                         empty_cell   
16                                         empty_cell   
17                                         empty_cell   
18                Прости меня, Господи, ибо грешен |    
19                                         empty_cell   

                             examples_and_definitions  
0   key word|english word|first word|good word|spe...  
1                                          empty_cell  
2                                      but | while |   
3                     He thinks of you day and night|  
4        It's an embarrassing joke and not an insult|  
5                 This is a squid and not an octopus|  
6      as | so | as well as | how | so that | both |   
7                                          emp

In [16]:
import gensim.downloader as api
from sklearn.metrics.pairwise import cosine_distances
from  sklearn.metrics.pairwise import cosine_similarity

from nltk import word_tokenize, pos_tag
from nltk.corpus import wordnet
from nltk.stem import WordNetLemmatizer 
lemmatizer = WordNetLemmatizer()
from nltk.corpus import stopwords
stopWords = set(stopwords.words('english'))
import math
import numpy as np

from tqdm import tqdm

In [2]:
model = api.load('glove-twitter-100')

In [3]:
l1 = "hello my friends"
l2 = "hello my girlfriend"

def get_wordnet_pos(treebank_tag):

    if treebank_tag.startswith('J'):
        return wordnet.ADJ
    elif treebank_tag.startswith('V'):
        return wordnet.VERB
    elif treebank_tag.startswith('N'):
        return wordnet.NOUN
    elif treebank_tag.startswith('R'):
        return wordnet.ADV
    else:
        return None
    
def get_nonstopwords_vectors_sum(lemm_list):
    orig_vector = np.zeros(shape = 100)
    for lemma in lemm_list:
        if lemma not in stopWords:
            #print (lemma)
            try:
                orig_vector += model[lemma]
            except:
                pass
    return orig_vector


def get_lemmatized_line(line):
    pos_tagged_ngramm = pos_tag(line.split())
    lemmatized_line_list = []
    for word_el in pos_tagged_ngramm:
        pos = get_wordnet_pos(word_el[1])
        if pos:
            lemma = lemmatizer.lemmatize(word_el[0], pos =pos)
        else:
            lemma = word_el[0]
        lemmatized_line_list.append(lemma)
    return lemmatized_line_list

get_lemmatized_line(l1)

def find_lines_similarity(line_1, line_2):
    lemmatized_l1_list = get_lemmatized_line(line_1)
    lemmatized_l2_list = get_lemmatized_line(line_2)
    #print(lemmatized_l1_list,lemmatized_l2_list )
    l1_vect = get_nonstopwords_vectors_sum(lemmatized_l1_list)
    l2_vect = get_nonstopwords_vectors_sum(lemmatized_l2_list)
    cos_sim = cosine_similarity(l1_vect.reshape(1, -1), l2_vect.reshape(1, -1))[0][0]
    #print(cos_sim)
    return cos_sim

find_lines_similarity(l1, l2)    
    

0.9236770700727499

In [7]:
cosine_similarity(model['mother'].reshape(1, -1), model['woman'].reshape(1, -1))[0][0]

0.7815035

In [ ]:
a = Nan
type(a)

In [13]:
def update_enf_word(dct_word, senseword, exmpl):
    #print(senseword)
    if senseword in dct_word:
        if exmpl == "empty_cell":
            #print("EMPTTY")
            pass
        else:
            dct_word[senseword]['examples'] += exmpl
    else:
        dct_word[senseword] = {}
        if exmpl == "empty_cell":
            #print("EMPTTY")
            dct_word[senseword]['examples'] = ''
        else:
            dct_word[senseword]['examples'] = exmpl

def csv_to_structure_dict(df):
    new_dict = {}
    for df_ind in range(len(df)):
        df_element = list(df.iloc[df_ind])
        eng_word = df_element[1]
        sense_word = df_element[2]
        examples_context = df_element[5]
        #print(df_element)
        if eng_word not in new_dict:
            new_dict[eng_word] = {}
            update_enf_word(new_dict[eng_word],sense_word, examples_context)
        else:
            update_enf_word(new_dict[eng_word],sense_word, examples_context)
    return new_dict
dct = csv_to_structure_dict(systran_en_ru)

In [11]:
dct['dinner']

{'ужин': {'examples': 'romantic dinner|gala dinner|family dinner|themed dinner|supper | meal | '},
 'обед': {'examples': 'business dinner|excellent dinner|lunch | meal | afternoon | lunchtime | '}}

In [14]:
dct_en_fr = csv_to_structure_dict(systran_en_fr)

In [10]:
dct_en_fr['dinner'] 

{'dîner': {'examples': 'gala dinner|romantic dinner|mess dinner|business dinners|diner | '},
 'soir': {'examples': 'evening | night | '},
 'souper': {'examples': 'formal dinner|group dinner|supper | diner | '},
 'repas': {'examples': 'theme dinners|medieval dinners|nice dinner|family dinner|meal | food | lunch | '}}

In [45]:
c1 = 'gala dinner|romantic dinner|mess dinner|business dinners|'
c2 = 'romantic dinner|gala dinner|family dinner|themed dinner|'
def get_context_similarity(ctx1, ctx2):
    simialrity_list = []
    #print("ctxs","\n", ctx1,"\n",ctx2 )
    #if "empty_cell" not in ctx1 and "empty_cell" not in ctx2:
    if len(ctx1) != 0 and len(ctx2) != 0:
        for ctx1_el in ctx1.split("|"):
            if ctx1_el.strip() != '':
                #print(ctx1_el)
                for ctx1_e2 in ctx2.split("|"):
                    if ctx1_e2.strip() != '': 
                        #print (ctx1_e2.strip())
                        sim = find_lines_similarity(ctx1_el, ctx1_e2) 
                        #print('SIM',ctx1_el, ctx1_e2,sim)
                        simialrity_list.append(sim)
        #print(simialrity_list)
        return np.mean(simialrity_list)
        #return np.median(simialrity_list)
    else:
        return "no_ctx"
    """
    elif "empty_cell" in ctx1 and "empty_cell" in ctx2:
        return "no_ctx_both"
    elif "empty_cell" in ctx1:
        return "no_ctx_l1"
    elif "empty_cell" in ctx2:
        return "no_ctx_l2"   
    """
get_context_similarity(c1, c2)        

0.8326094228960484

In [ ]:
"""
def average_similarity(ex_sim, ctx_sim,simil_dict, local_word, compared_word):
    print(local_word, compared_word)
    simil_dict[local_word][compared_word] = 'no_data_from_compared_word'
    if ex_sim == "no_ctx" and ctx_sim == "no_ctx":
        print("here==")
        simil_dict[local_word][compared_word] = "no_context_for_merge"
    elif ex_sim != "no_ctx" and ctx_sim == "no_ctx":
        simil_dict[local_word][compared_word] = ex_sim
        print("here!=",ex_sim)
    elif ex_sim == "no_ctx" and ctx_sim != "no_ctx":
        simil_dict[local_word][compared_word] = ctx_sim
        print("here=!",ctx_sim)
    else:
        simil_dict[local_word][compared_word] = (ex_sim + ctx_sim)/2
        print("here!!",ex_sim, ctx_sim, (ex_sim + ctx_sim)/2)
"""

In [47]:
def get_context_and_examples_sim(senseword_dict_l1, senseword_dict_l2, simil_dict_1,simil_dict_2, 
                                 loc_w_1, loc_w_2, print_output = True):
    if print_output: print(loc_w_1, senseword_dict_l1,"\n", loc_w_2, senseword_dict_l2)
    similarity = get_context_similarity(senseword_dict_l1['examples'], senseword_dict_l2['examples'])
    if print_output: print(loc_w_1, loc_w_2, "examples_sim", similarity,"\n")
        
    if similarity == "no_ctx":
        simil_dict_1[loc_w_1][loc_w_2] = 0
        simil_dict_2[loc_w_2][loc_w_1] = 0
    else:
        simil_dict_1[loc_w_1][loc_w_2] = similarity
        simil_dict_2[loc_w_2][loc_w_1] = similarity

        
def merge_two_lang_structures(original_eng_word, lang_dict_1, lang_dict_2,eng_word_df, l1_list_for_df,context_l1,  l2_list_for_df, context_l2):
    sim_dict_l1 = {}
    sim_dict_l2 = {}
    for local_1_senseword in lang_dict_1.keys():
        sim_dict_l1[local_1_senseword] = {}
        for local_2_senseword in lang_dict_2.keys():
            if local_2_senseword not in sim_dict_l2:
                sim_dict_l2[local_2_senseword] = {}
            sim = get_context_and_examples_sim(lang_dict_1[local_1_senseword], lang_dict_2[local_2_senseword],
                                              sim_dict_l1,sim_dict_l2, local_1_senseword, local_2_senseword)
            
            #break
        #break
    print("INNER_MERGER_DICT")
    print(sim_dict_l1)
    print()
    print(sim_dict_l2)
    print("=======\n")
    
    #MATCHING STRUCTURES FOR ONE ENGLISH WORD
    l1_to_l2_connect = {}
    l2_to_l1_connect = {}
    create_matching_structure(sim_dict_l1, sim_dict_l2,l1_to_l2_connect, l2_to_l1_connect)  
    merge_entities_lists(l1_to_l2_connect, l2_to_l1_connect, eng_word_df, l1_list_for_df, context_l1, l2_list_for_df, context_l2, original_eng_word)

def merge_two_dct(big_dict_l1, big_dict_l2):
    count = 0
    global_merged_dict= {}
    eng_word_for_df = []
    l1_list_for_df = [] 
    context_from_l1_list = []
    l2_list_for_df = []
    context_from_l2_list = []
    for eng_word in tqdm(list(big_dict_l1.keys())[15:]):
        print("pricessinf word", eng_word)
        #merge_two_lang_structures(eng_word, big_dict_l1[eng_word], big_dict_l2[eng_word],eng_word_for_df, l1_list_for_df, context_from_l1_list, l2_list_for_df, context_from_l2_list)
        try:
            merge_two_lang_structures(eng_word, big_dict_l1[eng_word], big_dict_l2[eng_word],eng_word_for_df, l1_list_for_df, context_from_l1_list, l2_list_for_df, context_from_l2_list)
        except:
            print(eng_word, 'MERGE_PROBLEM')
        count += 1
        #if count > 5: break
    print(len(eng_word_for_df), len(l1_list_for_df), len(l2_list_for_df))
    data = pd.DataFrame(list(zip(eng_word_for_df, l1_list_for_df,context_from_l1_list, l2_list_for_df, context_from_l2_list)),columns =['eng_word', 'l1','l1_context', 'l2','l2_context'])
    return  data   
df_all_words = merge_two_dct(dct,dct_en_fr)  



  0%|          | 0/228 [00:00<?, ?it/s]

pricessinf word treat
угощение {'examples': 'morning treat|feast | '} 
 friandise {'examples': 'real treat|natural pet treats|sweet | candy | delicacy | goody | pet treats | '}
угощение friandise examples_sim 0.47681965407522586 

угощение {'examples': 'morning treat|feast | '} 
 régal {'examples': 'real treat for the eyes|delight | feast | real treat | special treat | '}
угощение régal examples_sim 0.6433629414909723 

угощение {'examples': 'morning treat|feast | '} 
 gâterie {'examples': 'wholesome treat|sweet treats|'}
угощение gâterie examples_sim 0.6522174940844915 

угощение {'examples': 'morning treat|feast | '} 
 délice {'examples': 'delight | delicacy | bliss | delicious treats | '}
угощение délice examples_sim 0.4850717389295065 

угощение {'examples': 'morning treat|feast | '} 
 festin {'examples': 'feast | banquet | '}
угощение festin examples_sim 0.5637190528077038 

угощение {'examples': 'morning treat|feast | '} 
 douceur {'examples': 'softness | sweetness | sweet | gent

лечить traiter examples_sim 0.4257144472557444 

лечить {'examples': 'to treat people|heal | cure | heal | dose | '} 
 considérer {'examples': 'treated on a case-by-case basis|treated confidentially|treat as error|treated as a contempt|consider | regard | see | view | believe | look | think | feel | '}
лечить considérer examples_sim 0.4340303684917138 

лечить {'examples': 'to treat people|heal | cure | heal | dose | '} 
 soigner {'examples': 'to treat people|to treat angina|cure | heal | look after | care | look after | heal | care | '}
лечить soigner examples_sim 0.5391206474879421 

рассматривать {'examples': 'consider | see | view | regard | examine | review | '} 
 friandise {'examples': 'real treat|natural pet treats|sweet | candy | delicacy | goody | pet treats | '}
рассматривать friandise examples_sim 0.31434913320215746 

рассматривать {'examples': 'consider | see | view | regard | examine | review | '} 
 régal {'examples': 'real treat for the eyes|delight | feast | real treat 

рассматриваться gâterie examples_sim 0.3447770260030276 

рассматриваться {'examples': 'consider | view | address | examine | regard | see | review | construe | '} 
 délice {'examples': 'delight | delicacy | bliss | delicious treats | '}
рассматриваться délice examples_sim 0.23018502156309367 

рассматриваться {'examples': 'consider | view | address | examine | regard | see | review | construe | '} 
 festin {'examples': 'feast | banquet | '}
рассматриваться festin examples_sim 0.18936405946085968 

рассматриваться {'examples': 'consider | view | address | examine | regard | see | review | construe | '} 
 douceur {'examples': 'softness | sweetness | sweet | gentleness | mildness | smoothness | delicacy | meekness | kindness | '}
рассматриваться douceur examples_sim 0.09054272276820464 

рассматриваться {'examples': 'consider | view | address | examine | regard | see | review | construe | '} 
 émail {'examples': 'enamel | '}
рассматриваться émail examples_sim 0.06502803458890659 

рассма


  0%|          | 1/228 [00:03<12:30,  3.31s/it]

...


 99%|█████████▉| 226/228 [06:01<00:02,  1.20s/it]

максимум bon examples_sim 0.44986064807392584 

максимум {'examples': 'maximum | peak | high | '} 
 exemplaire {'examples': 'exemplary | outstanding | '}
максимум exemplaire examples_sim 0.2522152199070197 

максимум {'examples': 'maximum | peak | high | '} 
 optimal {'examples': 'optimal | optimum | maximum | best possible | '}
максимум optimal examples_sim 0.4467912346600212 

максимум {'examples': 'maximum | peak | high | '} 
 direct {'examples': 'direct | straightforward | '}
максимум direct examples_sim 0.20610094789927366 

максимум {'examples': 'maximum | peak | high | '} 
 bonne chance {'examples': 'best of luck|'}
максимум bonne chance examples_sim 0.42573392757524425 

максимум {'examples': 'maximum | peak | high | '} 
 maximum {'examples': 'maximum | utmost | minimum | peak | '}
максимум maximum examples_sim 0.5416207036880382 

максимум {'examples': 'maximum | peak | high | '} 
 bon voeu {'examples': ''}
максимум bon voeu examples_sim no_ctx 

максимум {'examples': 'maximum

хороший bon examples_sim 0.7682404542279029 

хороший {'examples': 'very good|really good|especially good|pretty good|nice | great | fine | '} 
 excellent {'examples': 'excellent | great | very good | outstanding | fine | '}
хороший excellent examples_sim 0.7262042716097471 

хороший {'examples': 'very good|really good|especially good|pretty good|nice | great | fine | '} 
 positif {'examples': 'particularly good|extremely good|positive | '}
хороший positif examples_sim 0.756287116394146 

хороший {'examples': 'very good|really good|especially good|pretty good|nice | great | fine | '} 
 beau {'examples': 'almost too good|fairly good|beautiful | nice | fine | lovely | great | attractive | pretty | wonderful | '}
хороший beau examples_sim 0.7739440920760792 

добрый {'examples': 'kind | good-natured | '} 
 bon {'examples': 'pretty good|so good|really good|good enough|best | better | right | bad | great | proper | improved | correct | '}
добрый bon examples_sim 0.29975433459408857 

добрый


100%|██████████| 228/228 [06:02<00:00,  1.59s/it]

правильный bon examples_sim 0.561603087036936 

правильный {'examples': 'right | correct | proper | true | appropriate | valid | accurate | '} 
 excellent {'examples': 'excellent | great | very good | outstanding | fine | '}
правильный excellent examples_sim 0.4991574413154549 

правильный {'examples': 'right | correct | proper | true | appropriate | valid | accurate | '} 
 positif {'examples': 'particularly good|extremely good|positive | '}
правильный positif examples_sim 0.5589121662908477 

правильный {'examples': 'right | correct | proper | true | appropriate | valid | accurate | '} 
 beau {'examples': 'almost too good|fairly good|beautiful | nice | fine | lovely | great | attractive | pretty | wonderful | '}
правильный beau examples_sim 0.5078861493838744 

INNER_MERGER_DICT
{'хороший': {'bon': 0.7682404542279029, 'excellent': 0.7262042716097471, 'positif': 0.756287116394146, 'beau': 0.7739440920760792}, 'добрый': {'bon': 0.29975433459408857, 'excellent': 0.2776173025395156, 'posi

In [63]:
dct['point']

{'точка': {'examples': 'starting point|access point|percentage point|ideal starting point|dot | spot | pixel | location | outlet | '},
 'пункт': {'examples': 'basis point|turning point|vaccination points|passport control points|item | post | paragraph | clause | pip | outlet | '},
 'момент': {'examples': 'tipping point|key point|important point|certain point|moment | time | thing | date | '},
 'очки': {'examples': 'ACP Point|bonus point|Reward Point|political point|glass | run | sunglasses | score | spectacle | goggle | eyeglass | Lounge Point | '},
 'балл': {'examples': 'penalty point|magnitude | score | vote | ball | grade | '},
 'смысл': {'examples': 'sense | meaning | way | implication | '},
 'дело': {'examples': 'case | affair | business | thing | matter | cause | work | ministry | '},
 'очко': {'examples': 'first point|run | pip | '},
 'указывать': {'examples': 'to point at the map|indicate | specify | show | suggest | point out | highlight | emphasize | '},
 'указать': {'example

In [53]:
dct_en_fr['dinner'] 

{'dîner': {'examples': 'gala dinner|romantic dinner|mess dinner|business dinners|diner | '},
 'soir': {'examples': 'evening | night | '},
 'souper': {'examples': 'formal dinner|group dinner|supper | diner | '},
 'repas': {'examples': 'theme dinners|medieval dinners|nice dinner|family dinner|meal | food | lunch | '}}

In [48]:
df_all_words.head(40)

eng_word               l1  \
0     treat          gâterie   
1     treat          gâterie   
2     treat          soigner   
3     treat          soigner   
4     treat       considérer   
5     treat       considérer   
6     treat       considérer   
7     treat       considérer   
8     treat          traiter   
9     treat        friandise   
10    treat            régal   
11    treat           délice   
12    treat           festin   
13    treat          douceur   
14    treat            émail   
15    treat          gâterie   
16    treat        friandise   
17    treat            régal   
18    treat           délice   
19    treat           festin   
20    treat          gâterie   
21    treat      no_equality   
22    treat          soigner   
23    treat       considérer   
24    treat       considérer   
25    treat       considérer   
26    treat          soigner   
27    treat       considérer   
28    treat      no_equality   
29    treat          traiter   
30    treat      no_equality   
31    diner            dîner   
32    diner          convive   
33    diner          couvert   
34    diner  café-restaurant   
35    diner           souper   
36    diner           dîneur   
37    diner      no_equality   
38   dinner            repas   
39   dinner            repas   

                                           l1_context               l2  \
0                       wholesome treat|sweet treats|         угощение   
1                       wholesome treat|sweet treats|     удовольствие   
2   to treat people|to treat angina|cure | heal | ...           лечить   
3   to treat people|to treat angina|cure | heal | ...         вылечить   
4   treated on a case-by-case basis|treated confid...    рассматривать   
5   treated on a case-by-case basis|treated confid...       относиться   
6   treated on a case-by-case basis|treated confid...       обращаться   
7   treated on a case-by-case basis|treated confid...  рассматриваться   
8   to treat cancer|to treat disease|to treat diab...     обрабатывать   
9   real treat|natural pet treats|sweet | candy | ...         угощение   
10  real treat for the eyes|delight | feast | real...         угощение   
11   delight | delicacy | bliss | delicious treats |          угощение   
12                                 feast | banquet |          угощение   
13  softness | sweetness | sweet | gentleness | mi...      no_equality   
14                                          enamel |       no_equality   
15                      wholesome treat|sweet treats|         угощение   
16  real treat|natural pet treats|sweet | candy | ...         угощение   
17  real treat for the eyes|delight | feast | real...         угощение   
18   delight | delicacy | bliss | delicious treats |          угощение   
19                                 feast | banquet |          угощение   
20                      wholesome treat|sweet treats|     удовольствие   
21                                               None        лакомство   
22  to treat people|to treat angina|cure | heal | ...           лечить   
23  treated on a case-by-case basis|treated confid...    рассматривать   
24  treated on a case-by-case basis|treated confid...       относиться   
25  treated on a case-by-case basis|treated confid...       обращаться   
26  to treat people|to treat angina|cure | heal | ...         вылечить   
27  treated on a case-by-case basis|treated confid...  рассматриваться   
28                                               None         угостить   
29  to treat cancer|to treat disease|to treat diab...     обрабатывать   
30                                               None         лечиться   
31                                          dinner |       no_equality   
32                                  guest | seater |       no_equality   
33  seat | cover | cutlery | canopy | place settin...      no_equality   
34  coffee shop | cafe-restaurant | café restauran...      no_equality   
35                        

In [31]:
df_all_words.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3076 entries, 0 to 3075
Data columns (total 5 columns):
eng_word      3076 non-null object
l1            3076 non-null object
l1_context    2310 non-null object
l2            3076 non-null object
l2_context    2410 non-null object
dtypes: object(5)
memory usage: 120.2+ KB


In [49]:
df_all_words.to_csv("systran_merge_mean_04_similarity.csv")

In [46]:
def merge_dicts(l1_l2_dict,l2_to_l1, l1_to_l2):
    for local_word_1 in l1_l2_dict.keys():
        sorted_sim = sorted(l1_l2_dict[local_word_1].items(), key=lambda kv: kv[1], reverse = True)
        if sorted_sim[0][1] < 0.4:
            print("no suitable connections for ", local_word_1)
            l1_to_l2[local_word_1] = ["no_equality"]
        else:
            if local_word_1 in l1_to_l2:
                if sorted_sim[0][0] not in l1_to_l2[local_word_1]:
                    l1_to_l2[local_word_1].append(sorted_sim[0][0])
            else:
                l1_to_l2[local_word_1] = []
                l1_to_l2[local_word_1].append(sorted_sim[0][0])
            print(local_word_1, "sorted_sim[0][1]",sorted_sim[0][1])
            
            if sorted_sim[0][0] in l2_to_l1:  
                if local_word_1 not in l2_to_l1[sorted_sim[0][0]]:
                    l2_to_l1[sorted_sim[0][0]].append(local_word_1)
            else:
                l2_to_l1[sorted_sim[0][0]] = []
                l2_to_l1[sorted_sim[0][0]].append(local_word_1)
                
ru_fr_dict = {'обойти': {'se promener': 0.16193252812028638, 'se balader': 0.15641367945030674, "s'éloigner": 0.162819447439424, 'promener': 0.16490256085461272}, 'вращаться': {'se promener': 0.4123024692238632, 'se balader': 0.36482488114980133, "s'éloigner": 0.19768349945429559, 'promener': 0.22889580396221318}, 'ездить по миру': {'se promener': 0, 'se balader': 0, "s'éloigner": 0, 'promener': 0}, 'часто путешествовать': {'se promener': 0, 'se balader': 0, "s'éloigner": 0, 'promener': 0}, 'хватать': {'se promener': 0.36273753561810446, 'se balader': 0.2975160600112141, "s'éloigner": 0.3047695342194968, 'promener': 0.29944649457673916}, 'пролетать': {'se promener': 0.6350658803284455, 'se balader': 0.3733952107024293, "s'éloigner": 0.4256126771370779, 'promener': 0.6414917193832451}, 'ходить вокруг': {'se promener': 0, 'se balader': 0, "s'éloigner": 0, 'promener': 0}}
fr_ru_dict = {'se promener': {'обойти': 0.16193252812028638, 'вращаться': 0.4123024692238632, 'ездить по миру': 0, 'часто путешествовать': 0, 'хватать': 0.36273753561810446, 'пролетать': 0.6350658803284455, 'ходить вокруг': 0}, 'se balader': {'обойти': 0.15641367945030674, 'вращаться': 0.36482488114980133, 'ездить по миру': 0, 'часто путешествовать': 0, 'хватать': 0.2975160600112141, 'пролетать': 0.3733952107024293, 'ходить вокруг': 0}, "s'éloigner": {'обойти': 0.162819447439424, 'вращаться': 0.19768349945429559, 'ездить по миру': 0, 'часто путешествовать': 0, 'хватать': 0.3047695342194968, 'пролетать': 0.4256126771370779, 'ходить вокруг': 0}, 'promener': {'обойти': 0.16490256085461272, 'вращаться': 0.22889580396221318, 'ездить по миру': 0, 'часто путешествовать': 0, 'хватать': 0.29944649457673916, 'пролетать': 0.6414917193832451, 'ходить вокруг': 0}}
def create_matching_structure(l1_l2_dict, l2_l1_dict, l1_to_l2, l2_to_l1):
    print("FIRST LANG TO SECOND")
    merge_dicts(l1_l2_dict, l1_to_l2, l2_to_l1)
    """
    for local_word_1 in l1_l2_dict.keys():
        sorted_sim = sorted(l1_l2_dict[local_word_1].items(), key=lambda kv: kv[1], reverse = True)
        print(local_word_1,)
        if sorted_sim[0][1] == "no_context_for_merge":
            l1_to_l2[local_word_1] = "no_equality"
        elif sorted_sim[0][1] <= 0.6:
            l1_to_l2[local_word_1] = "no_equality"
        else:
            l1_to_l2[local_word_1] = sorted_sim[0][0]
            #print(local_word_1, "sorted_sim[0][1]",sorted_sim[0][1])
            l2_to_l1[sorted_sim[0][0]] = local_word_1
    """
    print('\n',l1_to_l2)
    print()
    print(l2_to_l1)
    print("\nSECOND LANG TO FIRST")
    merge_dicts(l2_l1_dict, l2_to_l1, l1_to_l2)
    print('\n',l1_to_l2)
    print()
    print(l2_to_l1)
    print()
    

l1_to_l2_connect = {}
l2_to_l1_connect = {}

create_matching_structure(ru_fr_dict, fr_ru_dict,l1_to_l2_connect, l2_to_l1_connect)    
    

FIRST LANG TO SECOND
no suitable connections for  обойти
вращаться sorted_sim[0][1] 0.4123024692238632
no suitable connections for  ездить по миру
no suitable connections for  часто путешествовать
no suitable connections for  хватать
пролетать sorted_sim[0][1] 0.6414917193832451
no suitable connections for  ходить вокруг

 {'se promener': ['вращаться'], 'promener': ['пролетать']}

{'обойти': ['no_equality'], 'вращаться': ['se promener'], 'ездить по миру': ['no_equality'], 'часто путешествовать': ['no_equality'], 'хватать': ['no_equality'], 'пролетать': ['promener'], 'ходить вокруг': ['no_equality']}

SECOND LANG TO FIRST
se promener sorted_sim[0][1] 0.6350658803284455
no suitable connections for  se balader
s'éloigner sorted_sim[0][1] 0.4256126771370779
promener sorted_sim[0][1] 0.6414917193832451

 {'se promener': ['вращаться', 'пролетать'], 'promener': ['пролетать'], 'se balader': ['no_equality'], "s'éloigner": ['пролетать']}

{'обойти': ['no_equality'], 'вращаться': ['se promener'],

In [ ]:
l1_to_l2_connect

In [ ]:
l2_to_l1_connect

In [24]:
def get_context_from_global_variable_dict(eng_word,local_word):
    #print(dct[eng_word])
    #print(dct_en_fr[eng_word])
    l1_sensewords = list(dct[eng_word].keys())
    l2_sensewords = list(dct_en_fr[eng_word].keys())
    if local_word == "no_equality":
        pass
    elif local_word in l1_sensewords:
        print("all_clear", local_word)
        return dct[eng_word][local_word]['examples']
    elif local_word in l2_sensewords:
        print("all_clear", local_word)
        return dct_en_fr[eng_word][local_word]['examples']
    else:
        print("something_went_ne_tak_no_word_in_dict", local_word)
    #print(l1_sensewords)
    #print(l2_sensewords)
get_context_from_global_variable_dict("treat", "угощение")    
    

all_clear угощение


'morning treat|feast | '

In [22]:
def handle_pairs(l1_to_l2, handled_pairs, eng_word_list, l1_list,l1_cont, l2_list,l2_cont, english_word):
    for l1_word in l1_to_l2.keys():
        print(l1_word)
        for l2_word in l1_to_l2[l1_word]:
            pair = l1_word + "_" + l2_word
            if pair not in handled_pairs:
                eng_word_list.append(english_word)
                l1_list.append(l1_word)
                l1_context = get_context_from_global_variable_dict(english_word, l1_word)    
                l1_cont.append(l1_context)
                l2_list.append(l2_word)
                l2_context = get_context_from_global_variable_dict(english_word, l2_word) 
                l2_cont.append(l2_context)
                handled_pairs.append(pair)

In [ ]:
merge_entities_lists(l1_to_l2_connect, l2_to_l1_connect, eng_word_df, l1_list_for_df, l2_list_for_df)

In [21]:
def merge_entities_lists(l1_to_l2, l2_to_l1, eng_word_list, l1_list, l1_context, l2_list, l2_context, english_word):
    handled_pairs = []
    handle_pairs(l1_to_l2,handled_pairs,eng_word_list,l1_list,l1_context, l2_list, l2_context, english_word)
    handle_pairs(l2_to_l1,handled_pairs,eng_word_list, l2_list, l2_context, l1_list,l1_context,  english_word)                  
    

In [ ]:
def merge_entities(l1_to_l2, l2_to_l1):
    handled_pairs = []
    l1_line = []
    l2_line = []
    handle_pairs(l1_to_l2,handled_pairs,l1_line,l2_line)
    handle_pairs(l2_to_l1,handled_pairs,l2_line, l1_line)                  
    
    data = pd.DataFrame(list(zip(l1_line,l2_line)),columns =['l1', 'l2'])
    return  data

        
        
df_fin = merge_entities(l1_to_l2_connect, l2_to_l1_connect)
df_fin.head()       

In [ ]:
x = {1: 2, 3: 4, 4: 3, 2: 1, 0: 0}
sorted(x.items(), key=lambda kv: kv[1])

# evaluate empty lines

In [50]:
df_mean_4 = pd.read_csv("./reverse_connected_dicts/systran_merge_mean_04_similarity.csv")

In [51]:
df_mean_4.head()

Unnamed: 0 eng_word          l1  \
0           0    treat     gâterie   
1           1    treat     gâterie   
2           2    treat     soigner   
3           3    treat     soigner   
4           4    treat  considérer   

                                          l1_context             l2  \
0                      wholesome treat|sweet treats|       угощение   
1                      wholesome treat|sweet treats|   удовольствие   
2  to treat people|to treat angina|cure | heal | ...         лечить   
3  to treat people|to treat angina|cure | heal | ...       вылечить   
4  treated on a case-by-case basis|treated confid...  рассматривать   

                                          l2_context  
0                             morning treat|feast |   
1  pleasure | fun | satisfaction | enjoyment | am...  
2       to treat people|heal | cure | heal | dose |   
3                                     cure | heal |   
4  consider | see | view | regard | examine | rev...

In [57]:
len(df_mean_4[df_mean_4['l1']=="no_equality"]), len(df_mean_4[df_mean_4['l2']=="no_equality"]), len(df_mean_4)

(483, 460, 3465)

In [58]:
def calc_empty_entities(df):
    return (len(df[df['l1']=="no_equality"]) + len(df[df['l2']=="no_equality"]))/len(df)
calc_empty_entities(df_mean_4)



0.27215007215007214

In [60]:
df_med_3 = pd.read_csv("./reverse_connected_dicts/systran_merge_median_03_similarity.csv")
calc_empty_entities(df_med_3)

0.17593338705345152

In [61]:
df_med_4 = pd.read_csv("./reverse_connected_dicts/systran_merge_median_04_similarity.csv")
calc_empty_entities(df_med_4)

0.2779700115340254

In [62]:
df_med_5 = pd.read_csv("./reverse_connected_dicts/systran_merge_median_05_similarity.csv")
calc_empty_entities(df_med_5)


0.46553966189856955